# Example: Hyperparameter tuning
--------------------------------

This example shows an advanced example on how to optimize your model's hyperparameters for multi-metric runs.

Import the breast cancer dataset from [sklearn.datasets](https://scikit-learn.org/stable/datasets/index.html#wine-dataset). This is a small and easy to train dataset whose goal is to predict whether a patient has breast cancer or not.

## Load the data

In [1]:
# Import packages
from sklearn.datasets import load_breast_cancer
from optuna.distributions import IntDistribution
from atom import ATOMClassifier

In [2]:
# Load the data
X, y = load_breast_cancer(return_X_y=True)

## Run the pipeline

In [3]:
# Initialize atom
atom = ATOMClassifier(X, y, n_jobs=4, verbose=2, random_state=1)

<< ================== ATOM ================== >>

Configuration ==================== >>
Algorithm task: Binary classification.
Parallel processing with 4 cores.

Dataset stats ==================== >>
Shape: (569, 31)
Train set size: 456
Test set size: 113
-------------------------------------
Memory: 141.24 kB
Scaled: False
Outlier values: 167 (1.2%)



In [4]:
# Train a MultiLayerPerceptron model on two metrics
# using a custom number of hidden layers
atom.run(
    models="MLP",
    metric=["f1", "ap"],
    n_trials=10,
    est_params={"activation": "relu"},
    ht_params={
        "distributions": {
            "hidden_layer_1": IntDistribution(2, 4),
            "hidden_layer_2": IntDistribution(10, 20),
            "hidden_layer_3": IntDistribution(10, 20),
            "hidden_layer_4": IntDistribution(2, 4),
        }
    },
    errors='raise'
)


Training ========================= >>
Models: MLP
Metric: f1, ap


Running hyperparameter tuning for MultiLayerPerceptron...
| trial | hidden_layer_1 | hidden_layer_2 | hidden_layer_3 | hidden_layer_4 |      f1 | best_f1 |      ap | best_ap | time_trial | time_ht |    state |
| ----- | -------------- | -------------- | -------------- | -------------- | ------- | ------- | ------- | ------- | ---------- | ------- | -------- |
| 0     |              3 |             17 |             10 |              2 |  0.9464 |  0.9464 |  0.9844 |  0.9844 |     9.522s |  9.522s | COMPLETE |
| 1     |              2 |             11 |             12 |              3 |  0.9744 |  0.9744 |  0.9991 |  0.9991 |     9.369s | 18.891s | COMPLETE |
| 2     |              3 |             15 |             14 |              4 |  0.9915 |  0.9915 |  0.9978 |  0.9991 |    11.460s | 30.351s | COMPLETE |
| 3     |              2 |             19 |             10 |              4 |  0.9655 |  0.9915 |  0.9878 |  0.999

In [5]:
# For multi-metric runs, the selected best trial is the first in the Pareto front
atom.mlp.best_trial

FrozenTrial(number=8, state=1, values=[0.9914529914529915, 0.9997077732320282], datetime_start=datetime.datetime(2024, 3, 5, 12, 9, 40, 773486), datetime_complete=datetime.datetime(2024, 3, 5, 12, 9, 41, 379399), params={'hidden_layer_1': 4, 'hidden_layer_2': 15, 'hidden_layer_3': 17, 'hidden_layer_4': 2}, user_attrs={'estimator': MLPClassifier(hidden_layer_sizes=(4, 15, 17, 2), random_state=1)}, system_attrs={'nsga2:generation': 0}, intermediate_values={}, distributions={'hidden_layer_1': IntDistribution(high=4, log=False, low=2, step=1), 'hidden_layer_2': IntDistribution(high=20, log=False, low=10, step=1), 'hidden_layer_3': IntDistribution(high=20, log=False, low=10, step=1), 'hidden_layer_4': IntDistribution(high=4, log=False, low=2, step=1)}, trial_id=8, value=None)

In [6]:
atom.plot_pareto_front()

In [7]:
# If you are unhappy with the results, it's possible to conitnue the study
atom.mlp.hyperparameter_tuning(n_trials=5)

Running hyperparameter tuning for MultiLayerPerceptron...
| trial | hidden_layer_1 | hidden_layer_2 | hidden_layer_3 | hidden_layer_4 |      f1 | best_f1 |      ap | best_ap | time_trial | time_ht |    state |
| ----- | -------------- | -------------- | -------------- | -------------- | ------- | ------- | ------- | ------- | ---------- | ------- | -------- |
| 10    |              4 |             18 |             13 |              4 |  0.9831 |  0.9915 |  0.9997 |  0.9997 |     0.643s | 46.038s | COMPLETE |
| 11    |              2 |             14 |             19 |              2 |  0.9421 |  0.9915 |  0.9899 |  0.9997 |     0.602s | 46.641s | COMPLETE |
| 12    |              2 |             11 |             10 |              4 |  0.7733 |  0.9915 |    0.99 |  0.9997 |     0.622s | 47.262s | COMPLETE |
| 13    |              2 |             12 |             15 |              2 |  0.9558 |  0.9915 |  0.9985 |  0.9997 |     0.614s | 47.876s | COMPLETE |
| 14    |              3 |    

In [8]:
# The trials attribute gives an overview of the trial results
atom.mlp.trials

hidden_layer_1  hidden_layer_2  hidden_layer_3  hidden_layer_4  \
trial                                                                   
0                   3              17              10               2   
1                   2              11              12               3   
2                   3              15              14               4   
3                   2              19              10               4   
4                   3              16              11               2   
5                   4              20              13               4   
6                   4              19              10               2   
7                   2              19              11               3   
8                   4              15              17               2   
9                   4              19              10               4   
10                  4              18              13               4   
11                  2              14              19               2   
12                  2              11              10               4   
13                  2              12              15               2   
14                  3              11              16               4   

                                               estimator        f1   best_f1  \
trial                                                                          
0      MLPClassifier(hidden_layer_sizes=(3, 17, 10, 2...  0.946429  0.991453   
1      MLPClassifier(hidden_layer_sizes=(2, 11, 12, 3...  0.974359  0.991453   
2      MLPClassifier(hidden_layer_sizes=(3, 15, 14, 4...  0.991453  0.991453   
3      MLPClassifier(hidden_layer_sizes=(2, 19, 10, 4...  0.965517  0.991453   
4      MLPClassifier(hidden_layer_sizes=(3, 16, 11, 2...  0.966102  0.991453   
5      MLPClassifier(hidden_layer_sizes=(4, 20, 13, 4...  0.973913  0.991453   
6      MLPClassifier(hidden_layer_sizes=(4, 19, 10, 2...  0.982759  0.991453   
7      MLPClassifier(hidden_layer_sizes=(2, 19, 11, 3...  0.773333  0.991453   
8      MLPClassifier(hidden_layer_sizes=(4, 15, 17, 2...  0.991453  0.991453   
9      MLPClassifier(hidden_layer_sizes=(4, 19, 10, 4...  0.982759  0.991453   
10     MLPClassifier(hidden_layer_sizes=(4, 18, 13, 4...  0.983051  0.991453   
11     MLPClassifier(hidden_layer_sizes=(2, 14, 19, 2...  0.942149  0.991453   
12     MLPClassifier(hidden_layer_sizes=(2, 11, 10, 4...  0.773333  0.991453   
13     MLPClassifier(hidden_layer_sizes=(2, 12, 15, 2...  0.955752  0.991453   
14     MLPClassifier(hidden_layer_sizes=(3, 11, 16, 4...  0.773333  0.991453   

             ap   best_ap  time_trial    time_ht     state  
trial                                                       
0      0.984402  0.999708    9.522182   9.522182  COMPLETE  
1      0.999128  0.999708    9.368656  18.890838  COMPLETE  
2      0.997842  0.999708   11.459907  30.350745  COMPLETE  
3      0.987805  0.999708   11.358701  41.709446  COMPLETE  
4      0.998086  0.999708    0.652744  42.362190  COMPLETE  
5      0.998855  0.999708    0.610210  42.972400  COMPLETE  
6      0.990748  0.999708    0.605815  43.578215  COMPLETE  
7      0.999708  0.999708    0.601119  44.179334  COMPLETE  
8      0.999708  0.999708    0.605913  44.785247  COMPLETE  
9      0.982168  0.999708    0.610058  45.395305  COMPLETE  
10     0.999708  0.999708    0.642812  46.038117  COMPLETE  
11     0.989914  0.999708    0.602385  46.640502  COMPLETE  
12     0.990024  0.999708    0.621954  47.262456  COMPLETE  
13     0.998518  0.999708    0.613556  47.876012  COMPLETE  
14     0.972070  0.999708    0.622326  48.498338  COMPLETE

In [9]:
# Select a custom best trial...
atom.mlp.best_trial = 2

# ...and check that the best parameters are now those in the selected trial
atom.mlp.best_params

{'hidden_layer_sizes': (3, 15, 14, 4)}

In [10]:
# Lastly, fit the model on the complete training set 
# using the new combination of hyperparameters
atom.mlp.fit()

Fit ---------------------------------------------
Train evaluation --> f1: 0.9983   ap: 0.9998
Test evaluation --> f1: 0.9718   ap: 0.9947
Time elapsed: 3.541s


## Analyze the results

In [11]:
atom.plot_trials()

In [12]:
atom.plot_parallel_coordinate()